In [1]:
import librosa
import pandas as pd
import os
import numpy as np
from tqdm import tqdm

from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import LabelEncoder

import tensorflow as tf
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense , Activation , Dropout

import IPython.display as ipd

In [2]:
path = '../input/urbansound8k'

df = pd.read_csv('../input/urbansound8k/UrbanSound8K.csv')
df


slice_file_name    fsID       start         end  salience  fold  \
0       100032-3-0-0.wav  100032    0.000000    0.317551         1     5   
1     100263-2-0-117.wav  100263   58.500000   62.500000         1     5   
2     100263-2-0-121.wav  100263   60.500000   64.500000         1     5   
3     100263-2-0-126.wav  100263   63.000000   67.000000         1     5   
4     100263-2-0-137.wav  100263   68.500000   72.500000         1     5   
...                  ...     ...         ...         ...       ...   ...   
8727     99812-1-2-0.wav   99812  159.522205  163.522205         2     7   
8728     99812-1-3-0.wav   99812  181.142431  183.284976         2     7   
8729     99812-1-4-0.wav   99812  242.691902  246.197885         2     7   
8730     99812-1-5-0.wav   99812  253.209850  255.741948         2     7   
8731     99812-1-6-0.wav   99812  332.289233  334.821332         2     7   

      classID             class  
0           3          dog_bark  
1           2  children_playing  
2           2  children_playing  
3           2  children_playing  
4           2  children_playing  
...       ...               ...  
8727        1          car_horn  
8728        1          car_horn  
8729        1          car_horn  
8730        1          car_horn  
8731        1          car_horn  

[8732 rows x 8 columns]

In [3]:
def features_extract(file):
    audio,sample_rate = librosa.load(file_name,res_type='kaiser_fast')
    feature = librosa.feature.mfcc(y=audio,sr=sample_rate,n_mfcc=50)
    scaled_feature = np.mean(feature.T,axis=0)
    return scaled_feature

extracted = []

for index_num,row in tqdm(df.iterrows()):
    file_name = os.path.join(os.path.abspath(path),'fold'+str(row["fold"])+'/',str(row['slice_file_name'])) 
    final_class_labels = row['class']   
    data= features_extract(file_name)    
    extracted.append([data,final_class_labels])


3555it [07:21,  6.86it/s]/opt/conda/lib/python3.7/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=1323
  return f(*args, **kwargs)
8326it [16:54, 13.61it/s]/opt/conda/lib/python3.7/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=1103
  return f(*args, **kwargs)
/opt/conda/lib/python3.7/site-packages/librosa/util/decorators.py:88: UserWarning: n_fft=2048 is too small for input signal of length=1523
  return f(*args, **kwargs)
8732it [17:41,  8.22it/s]


In [4]:

ext_df = pd.DataFrame(extracted,columns=['feature','class'])
ext_df


feature             class
0     [-218.18938, 71.38549, -131.49442, -52.25892, ...          dog_bark
1     [-425.05234, 110.67095, -54.192833, 62.045414,...  children_playing
2     [-459.82623, 122.82864, -47.908062, 53.302677,...  children_playing
3     [-414.82184, 102.94826, -36.656853, 54.170742,...  children_playing
4     [-447.60776, 115.08627, -53.74607, 61.55309, 1...  children_playing
...                                                 ...               ...
8727  [-399.52393, 136.84413, -51.97703, 37.01486, -...          car_horn
8728  [-347.3277, 87.53585, -46.2994, 52.748062, -33...          car_horn
8729  [-304.84702, 112.69567, -47.21992, 37.061134, ...          car_horn
8730  [-345.06885, 126.78658, -56.18254, 36.07703, -...          car_horn
8731  [-316.331, 95.86536, -38.176315, 47.640114, -7...          car_horn

[8732 rows x 2 columns]

In [5]:
x = np.array(ext_df['feature'].tolist())
y = np.array(ext_df['class'].tolist())


In [6]:
le = LabelEncoder()

y = to_categorical(le.fit_transform(y))


In [7]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state = 42)

print("Number of training samples = ", x_train.shape[0])
print("Number of testing samples = ",x_test.shape[0])


Number of training samples =  6985
Number of testing samples =  1747


In [8]:
num_labels = y.shape[1]
model = Sequential()

model.add(Dense(128, input_shape=(50,)))
model.add(Activation('relu'))
model.add(Dropout(0.5))

model.add(Dense(256))
model.add(Activation('relu'))
model.add(Dropout(0.5))
model.add(Dense(256))
model.add(Activation('relu'))
model.add(Dropout(0.5))
model.add(Dense(128))

model.add(Dense(num_labels))
model.add(Activation('softmax'))
model.summary()


Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 128)               6528      
_________________________________________________________________
activation (Activation)      (None, 128)               0         
_________________________________________________________________
dropout (Dropout)            (None, 128)               0         
_________________________________________________________________
dense_1 (Dense)              (None, 256)               33024     
_________________________________________________________________
activation_1 (Activation)    (None, 256)               0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 256)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 256)               6

2022-06-30 06:29:34.590816: I tensorflow/core/common_runtime/process_util.cc:146] Creating new thread pool with default inter op setting: 2. Tune using inter_op_parallelism_threads for best performance.


In [9]:
model.compile(optimizer=tf.keras.optimizers.Adam(),loss=tf.keras.losses.CategoricalCrossentropy(),metrics=['accuracy'])

In [10]:
num_epochs = 150
num_batch_size = 32

model.fit(
          x_train, 
          y_train, 
          batch_size=num_batch_size, 
          epochs=num_epochs,
          validation_data=(x_test, y_test),
         )


2022-06-30 06:29:37.076609: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:185] None of the MLIR Optimization Passes are enabled (registered 2)


Epoch 1/150
219/219 [==============================] - 2s 5ms/step - loss: 9.0556 - accuracy: 0.1509 - val_loss: 2.1058 - val_accuracy: 0.2433
Epoch 2/150
219/219 [==============================] - 1s 4ms/step - loss: 2.3801 - accuracy: 0.2074 - val_loss: 2.1040 - val_accuracy: 0.1992
Epoch 3/150
219/219 [==============================] - 1s 4ms/step - loss: 2.0856 - accuracy: 0.2545 - val_loss: 1.9738 - val_accuracy: 0.2616
Epoch 4/150
219/219 [==============================] - 1s 4ms/step - loss: 1.9930 - accuracy: 0.2908 - val_loss: 1.8069 - val_accuracy: 0.3423
Epoch 5/150
219/219 [==============================] - 1s 4ms/step - loss: 1.8616 - accuracy: 0.3319 - val_loss: 1.7077 - val_accuracy: 0.3858
Epoch 6/150
219/219 [==============================] - 1s 4ms/step - loss: 1.7896 - accuracy: 0.3679 - val_loss: 1.6258 - val_accuracy: 0.4190
Epoch 7/150
219/219 [==============================] - 1s 4ms/step - loss: 1.7078 - accuracy: 0.3997 - val_loss: 1.5824 - val_accuracy: 0.4476

In [11]:
def extract_feature(file_name):
    audio_data, sample_rate = librosa.load(file_name, res_type='kaiser_fast') 
    fea = librosa.feature.mfcc(y=audio_data, sr=sample_rate, n_mfcc=50)
    scaled = np.mean(fea.T,axis=0)
    return np.array([scaled])


In [12]:
def print_prediction(file_name):
    pred_fea = extract_feature(file_name) 
    pred_vector = np.argmax(model.predict(pred_fea), axis=-1)
    pred_class = le.inverse_transform(pred_vector)
    print("The predicted class is:", pred_class[0], '\n') 


In [13]:
file_name = '../input/urbansound8k/fold2/100652-3-0-2.wav'

print_prediction(file_name)

ipd.Audio(file_name)


The predicted class is: dog_bark 



In [14]:
file_name = '../input/urbansound8k/fold6/101281-3-0-14.wav'

print_prediction(file_name)

ipd.Audio(file_name)

The predicted class is: drilling 



In [15]:
file_name = '../input/urbansound8k/fold7/101848-9-0-8.wav'

print_prediction(file_name)

ipd.Audio(file_name)

The predicted class is: street_music 



In [16]:
file_name = '../input/urbansound8k/fold9/101729-0-0-17.wav'

print_prediction(file_name)

ipd.Audio(file_name)

The predicted class is: air_conditioner 



In [17]:
file_name = '../input/urbansound8k/fold5/100263-2-0-3.wav'

print_prediction(file_name)

ipd.Audio(file_name)

The predicted class is: children_playing 

